In [ ]:
# 
# CL-Metrics-Avalanche-DatasetB-4classes.ipynb
# 
# Author(s):
# Lan Mei <lanmei@student.ethz.ch>
#
# ======================================================================
# 
# Copyright (c) 2024 ETH Zurich.
# 
# Licensed under the Apache License, Version 2.0 (the "License");
# you may not use this file except in compliance with the License.
# You may obtain a copy of the License at
# 
# http://www.apache.org/licenses/LICENSE-2.0
# 
# Unless required by applicable law or agreed to in writing, software
# distributed under the License is distributed on an "AS IS" BASIS,
# WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
# See the License for the specific language governing permissions and
# limitations under the License.
# SPDX-License-Identifier: Apache-2.0

In [10]:
import numpy as np

from pyexpat import model
import torch
import torch.nn as nn
import torch.optim as optim
import torch as t
import torch.nn.functional as F
import json
import random
from torchvision.transforms import Compose

import os
from os import path, walk
import pandas as pd
from scipy import signal

CUR_FOLDER = os.path.abspath("")

# Dataset B downloaded from the link in README.md and put into the "data" folder. Note that binary files should be converted to csv files.
DATASET_1_PATH = CUR_FOLDER + "/data/DatasetB/SubjectA_1129_S1/MM/csv/" 
DATASET_2_PATH = CUR_FOLDER + "/data/DatasetB/SubjectA_1206_S2/MM/csv/" 
DATASET_3_PATH = CUR_FOLDER + "/data/DatasetB/SubjectA_1213_S3/MM/csv/" 
DATASET_4_PATH = CUR_FOLDER + "/data/DatasetB/SubjectA_1220_S4/MM/csv/" 
CONFIG_PATH =  CUR_FOLDER + "/config_avalanche_4classes.json"

with open(CONFIG_PATH) as fp:
    config = json.load(fp)

In [11]:
# filters
def notch_multiEEG(data,fs):
    '''
    50Hz multi channel EEG
    
    Params
    ------
    data: np array (n_ch,n_s)
        EEG data
    fs: float
        sampling frequency
    
    Return
    ------
    data_filt: np array (n_ch, n_s)
        filtered EEG data 
    '''
    
    w0 = 50/(fs/2)
    Q = 30
    notch_filter_50Hz = signal.iirnotch(w0, Q)

    
    data_filt = np.zeros(data.shape)
    for chan in range(data.shape[0]):
         
        data_filt[chan, :]= signal.lfilter(*notch_filter_50Hz, data[chan, :])
        
    return data_filt

    
def bandpass_multiEEG(data, fs, f_low, f_high, order):
    '''
    Bandpass multi channel EEG
    
    Params
    ------
    data: np array (n_ch,n_s)
        EEG data
    f_low: float
        lower corner frequency [Hz]
    f_high: float
        upper corner_frequency [Hz]
    fs: float
        sampling frequency
    
    Return
    ------
    data_filt: np array (n_ch, n_s)
        filtered EEG data 
    '''

    nyq = 0.5 * fs
    low_freq = f_low / nyq
    high_freq = f_high / nyq
    filt_coef = signal.butter(N=order, Wn=[low_freq, high_freq], btype='bandpass', output='sos')
    
    for chan in range(data.shape[0]):
        data[chan, :] = signal.sosfilt(filt_coef, data[chan, :])
    return data


In [12]:
def get_data(directory, n_files, fs, filter_config, ds=1):
    '''
    Preprocess and obtain the data
    
    Params
    ------
    directory: string
        location of the csv files of data
    n_files: int
        number of files in the directory
    fs: int
        sampling frequency [Hz]
    filter_config: dictionary
        configuration of filter
    ds: int
        downsampling rate
    
    Return
    ------
    data_filt: np array 
        data and labels
    '''
    
    intertrial_sec = 4  # at least 4 seconds between trials
    samples_stimulus = 1950 # stimulus is 2000 samples, but some are lost due to transmission errors
    offset_sec = -5  # startpoint for the stimulus to load. choose time window (0,samples_sec) for classification in config file: t1_factor, t2_factor
    offset = int(fs * offset_sec)  # number of samples how much later than the stimulus a trial starts
    samples = samples_stimulus - offset  # number of samples of trial before cut
    intertrial = int(fs * intertrial_sec)  # number of samples in between trials
    number_of_trials = 40 # 4-classes: 4*10, 2-classes: 2*10

    # trigger values
    trigger_left = 50
    trigger_right = 60
    trigger_tongue = 70
    trigger_nothing = 100

    # labels for classifier
    lb_nothing = 0
    lb_left = 1
    lb_right = 2
    lb_tongue = 3

    N_ch = 8

    number_of_runs = n_files

    file_index = 0
    runs = np.zeros((number_of_runs, number_of_trials, N_ch, samples), dtype=np.float32)
    y_runs = np.zeros((number_of_runs, number_of_trials), dtype=np.float32)

    preprocess_mean = 0
    
    valid_trials = 0
    
    for root, dirs, files in walk(directory):
        for file in files:
            print(file)
            file_path = path.join(root, file)
            df = pd.read_csv(file_path,sep=',')
            data = df.to_numpy(dtype=np.float32)
            X = np.transpose(data[:,:]) # X: [channels+triggers, samples]
            temp_afterfilt_X = X[:-1,:].copy()
            temp_afterfilt_X = notch_multiEEG(temp_afterfilt_X, fs)
            temp_afterfilt_X = bandpass_multiEEG(temp_afterfilt_X, fs, filter_config['fc_low'], filter_config['fc_high'],
                                              filter_config['order'])
            
            # Subtracting moving avg.
            N = int(250/2)
            for i in range(N_ch):
                temp_afterfilt_X_moving_avg = np.convolve(temp_afterfilt_X[i], np.ones(N)/N, mode='same')
                temp_afterfilt_X[i] = temp_afterfilt_X[i] - temp_afterfilt_X_moving_avg
            
            trials = np.zeros((number_of_trials, N_ch, samples), dtype=np.float32)
            y = np.zeros(number_of_trials, dtype=np.float32) # to store the labels
            
            n_samples=X.shape[1] # number of samples in the run
            k = 0 # trial
            sample = 0
            
            while sample < n_samples:
                # four class classification
                if X[-1, sample] == trigger_left:  # left hand MM
                    start_trial = sample + offset  
                    stop_trial = start_trial + samples  
                    temp_filt = temp_afterfilt_X[0:N_ch, start_trial:stop_trial]  

                    trials[k] = temp_filt
                    y[k] = lb_left 
                    y[k] = y[k] - 1 
                    sample = sample + samples_stimulus + intertrial  # skip to the next sample
                    k += 1  # go to the next trial
                    valid_trials += 1

                elif X[-1, sample] == trigger_right:  # right hand MM
                    start_trial = sample + offset
                    stop_trial = start_trial + samples 
                    temp_filt = temp_afterfilt_X[0:N_ch, start_trial:stop_trial] 

                    trials[k] = temp_filt
                    y[k] = lb_right
                    y[k] = y[k] - 1 
                    sample = sample + samples_stimulus + intertrial  # skip to the next sample
                    k += 1  # go to the next trial
                    valid_trials += 1
                    
                elif X[-1, sample] == trigger_nothing:  # rest
                    start_trial = sample + offset  
                    stop_trial = start_trial + samples  
                    temp_filt = temp_afterfilt_X[0:N_ch, start_trial:stop_trial]  
                    
                    trials[k] = temp_filt
                    y[k] = lb_nothing  
                    y[k] = y[k] + 3  
                    sample = sample + samples_stimulus + intertrial  # skip to the next sample
                    k += 1  # go to the next trial
                    valid_trials += 1

                elif X[-1, sample] == trigger_tongue:  # tongue MM
                    start_trial = sample + offset  
                    stop_trial = start_trial + samples  
                    temp_filt = temp_afterfilt_X[0:N_ch, start_trial:stop_trial] 
                    
                    trials[k] = temp_filt
                    y[k] = lb_tongue 
                    y[k] = y[k] - 1  
                    sample = sample + samples_stimulus + intertrial  # skip to the next sample
                    k += 1  # go to the next trial
                    valid_trials += 1
                    
                ## Needed only for downsampling 
                # if ds > 1:
                #     samples_ds = int(np.ceil(samples / ds))
                #     X_ds = np.zeros((N_ch, samples_ds), dtype=np.float64)
                #     for chan in range(N_ch):
                #         X_ds[chan] = signal.decimate(trial[chan, :], ds)
                #     trial = X_ds

                else:
                    sample += 1  # go to the next sample

            runs[file_index] = trials
            y_runs[file_index] = y
            file_index += 1

    X = runs.reshape(number_of_runs * number_of_trials, N_ch, samples)
    y = y_runs.reshape(number_of_runs * number_of_trials)


    if ds > 1:
        samples_ds = int(np.ceil(samples / ds))
        X_ds = np.zeros((number_of_runs * number_of_trials, N_ch, samples_ds), dtype=np.float32)
        for trial in range(number_of_runs * number_of_trials):
            for chan in range(N_ch):
                X_ds[trial, chan] = signal.decimate(X[trial, chan, :], ds)
        X = X_ds

    print(valid_trials)
    if valid_trials != number_of_runs * number_of_trials:
        X_new_shape = np.zeros((valid_trials, N_ch, samples))
        y_new_shape = np.zeros((valid_trials))
        new_trial_idx = 0
        for trial_idx in range(number_of_runs * number_of_trials):
            if np.any(X[trial_idx]):
                X_new_shape[new_trial_idx] = X[trial_idx]
                y_new_shape[new_trial_idx] = y[trial_idx]
                new_trial_idx += 1
                
        X = X_new_shape
        y = y_new_shape
        
    print(X.shape)
                
    return X,y


In [13]:
class BCI_Drone(t.utils.data.Dataset):

    def __init__(self, root, fs=500, transform=None, filter_config=None, ds=1):
        self.root = root
        self.fs = fs
        self.transform = transform
        self.filter_config = filter_config
        self.ds = ds
        self.samples, self.labels = self._load_data()

    def __len__(self):  
        return len(self.samples)

    def __getitem__(self, idx):  

        sample = self.samples[idx, :, :]
        label = self.labels[idx]

        if self.transform:
            sample = self.transform(sample)
        return sample, label

    def _load_data(self):
        n_files = len(os.listdir(self.root))
        X, y = get_data(self.root, n_files, self.fs, self.filter_config, self.ds)

        data_return = t.Tensor(X).to(dtype=t.float)
        class_return = t.Tensor(y).to(dtype=t.long)

        return data_return, class_return

In [14]:
class Identity(object):

    def __call__(self, sample):
        return sample


class TimeWindowPostCue(object):

    def __init__(self, fs, t1_factor, t2_factor):
        self.t1 = int(t1_factor * fs)
        self.t2 = int(t2_factor * fs)

    def __call__(self, sample):
        return sample[:, :, self.t1:self.t2]


class ReshapeTensor(object):
    def __call__(self, sample):
        return sample.view(1, sample.shape[0], sample.shape[1])
    
class ReshapeFinal(object):
    def __call__(self, sample):
        return sample.view(1, -1)

class PaddingTensor(object):
    def __init__(self, padding):
        self.padding = int(padding)

    def __call__(self, sample):
        if self.padding == 0:
            return sample

        sample_pad = np.zeros((sample.shape[0], sample.shape[1], sample.shape[2] + self.padding), dtype=np.float32)
        for i in range(sample_pad.shape[0]):
            for ch in range(sample_pad.shape[1]):
                for j in range(sample.shape[2]):
                    sample_pad[i, ch, j] = sample[i, ch, j]

        return sample_pad

def get_transform(fs, t1_factor, t2_factor, filter_config, padding=0):
    if filter_config is None:
        filter_config = {'type': None}
    elif 'type' not in filter_config:
        filter_config['type'] = 'none'

    if padding is None:
        padding = 0

    return Compose([ReshapeTensor(),
                    TimeWindowPostCue(fs, t1_factor, t2_factor),
                    PaddingTensor(padding)])

def load_data(dir_data, data_config):
    try:
        padding = data_config['padding']
    except:
        padding = 0
    transform      = get_transform(data_config['fs'], data_config['t1_factor'],
                                   data_config['t2_factor'], data_config['filter'], padding)
    loaded_data  = BCI_Drone(root=dir_data, fs=data_config['fs'], transform=transform, filter_config = data_config['filter'], ds = data_config['ds'])
    return loaded_data


In [15]:
manualSeed = 4
torch.manual_seed(manualSeed)
random.seed(manualSeed)
np.random.seed(manualSeed)
# using GPU
torch.cuda.manual_seed(manualSeed)
torch.cuda.manual_seed_all(manualSeed)
# using cudnn
torch.backends.cudnn.enabled = False 
torch.backends.cudnn.benchmark = False
torch.backends.cudnn.deterministic = True
# dataloader number of workers 0, if > 0 background processes with their own seeds are started
nb_workers = 0
def _init_fn():
    np.random.seed(manualSeed)
    

In [16]:
dataset_1129_MM_A = load_data(DATASET_1_PATH, config['treat']['data'])
dataset_1206_MM_A = load_data(DATASET_2_PATH, config['treat']['data'])
dataset_1213_MM_A = load_data(DATASET_3_PATH, config['treat']['data'])
dataset_1220_MM_A = load_data(DATASET_4_PATH, config['treat']['data'])

Data_20231129_114031_A_S1_MM_1.csv
Data_20231129_115426_A_S1_MM_2.csv
Data_20231129_121012_A_S1_MM_3.csv
Data_20231129_122414_A_S1_MM_4.csv
Data_20231129_123859_A_S1_MM_5.csv
200
(200, 8, 4450)
Data_20231206_111947_MM_1_2.csv
Data_20231206_113703_MM_2_2.csv
Data_20231206_115349_MM_3_2.csv
Data_20231206_121643_MM_4_2.csv
Data_20231206_123226_MM_5_2.csv
200
(200, 8, 4450)
Data_20231213_103954_MM_1_2.csv
Data_20231213_110021_MM_2_2.csv
Data_20231213_111803_MM_3_2.csv
Data_20231213_113815_MM_4_2.csv
Data_20231213_115714_MM_5_2.csv
200
(200, 8, 4450)
Data_20231220_103456_MM_1_2.csv
Data_20231220_105828_MM_2_2.csv
Data_20231220_111706_MM_3_2.csv
Data_20231220_114136_MM_4_2.csv
Data_20231220_115909_MM_5_2.csv
200
(200, 8, 4450)


In [21]:
from avalanche.benchmarks.utils import AvalancheDataset

from avalanche.benchmarks.utils import make_classification_dataset

#train on all data, test on last 2 runs in S1
train_size_1129 = int(0.6 * len(dataset_1129_MM_A.labels))
test_size_1129 = len(dataset_1129_MM_A.labels) - train_size_1129
test_dataset_1129 = torch.utils.data.Subset(dataset_1129_MM_A, list(range(train_size_1129, train_size_1129+test_size_1129)))

test_dataset_1129.targets = dataset_1129_MM_A.labels[test_dataset_1129.indices]

avalanche_test_dataset_1129 = make_classification_dataset(test_dataset_1129, task_labels=0)

dataset_1129_MM_A.targets = dataset_1129_MM_A.labels

avalanche_train_dataset_1129_full_pretrained = make_classification_dataset(dataset_1129_MM_A, task_labels=0)

# t3v2 in S2
train_size_1206 = int(0.6 * len(dataset_1206_MM_A.labels))
test_size_1206 = len(dataset_1206_MM_A.labels) - train_size_1206
train_dataset_1206 = torch.utils.data.Subset(dataset_1206_MM_A, list(range(0, train_size_1206)))
test_dataset_1206 = torch.utils.data.Subset(dataset_1206_MM_A, list(range(train_size_1206, train_size_1206+test_size_1206)))

train_dataset_1206.targets = dataset_1206_MM_A.labels[train_dataset_1206.indices]
test_dataset_1206.targets = dataset_1206_MM_A.labels[test_dataset_1206.indices]

avalanche_train_dataset_1206 = make_classification_dataset(train_dataset_1206, task_labels=0)
avalanche_test_dataset_1206 = make_classification_dataset(test_dataset_1206, task_labels=0)

# t3v2 in S3
train_size_1213 = int(0.6 * len(dataset_1213_MM_A.labels))
test_size_1213 = len(dataset_1213_MM_A.labels) - train_size_1213
train_dataset_1213 = torch.utils.data.Subset(dataset_1213_MM_A, list(range(0, train_size_1213)))
test_dataset_1213 = torch.utils.data.Subset(dataset_1213_MM_A, list(range(train_size_1213, train_size_1213+test_size_1213)))

train_dataset_1213.targets = dataset_1213_MM_A.labels[train_dataset_1213.indices]
test_dataset_1213.targets = dataset_1213_MM_A.labels[test_dataset_1213.indices]

avalanche_train_dataset_1213 = make_classification_dataset(train_dataset_1213, task_labels=0)
avalanche_test_dataset_1213 = make_classification_dataset(test_dataset_1213, task_labels=0)

# t3v2 in S4
train_size_1220 = int(0.6 * len(dataset_1220_MM_A.labels))
test_size_1220 = len(dataset_1220_MM_A.labels) - train_size_1220
train_dataset_1220 = torch.utils.data.Subset(dataset_1220_MM_A, list(range(0, train_size_1220)))
test_dataset_1220 = torch.utils.data.Subset(dataset_1220_MM_A, list(range(train_size_1220, train_size_1220+test_size_1220)))

train_dataset_1220.targets = dataset_1220_MM_A.labels[train_dataset_1220.indices]
test_dataset_1220.targets = dataset_1220_MM_A.labels[test_dataset_1220.indices]

avalanche_train_dataset_1220 = make_classification_dataset(train_dataset_1220, task_labels=0)
avalanche_test_dataset_1220 = make_classification_dataset(test_dataset_1220, task_labels=0)

dataset_1129_MM_A.targets = dataset_1129_MM_A.labels

avalanche_train_dataset_1129_full_pretrained = make_classification_dataset(dataset_1129_MM_A, task_labels=0)

In [ ]:
from avalanche.benchmarks.generators import nc_benchmark, ni_benchmark, dataset_benchmark

scenario = dataset_benchmark(
    [avalanche_train_dataset_1129_full_pretrained, avalanche_train_dataset_1206, avalanche_train_dataset_1213, avalanche_train_dataset_1220], [avalanche_test_dataset_1129, avalanche_test_dataset_1206, avalanche_test_dataset_1213, avalanche_test_dataset_1220]
)

train_stream = scenario.train_stream

for experience in train_stream:
    task = experience.task_label
    exp_id = experience.current_experience
    training_dataset = experience.dataset
    print('Task {} batch {} -> train'.format(task, exp_id))
    print('This batch contains', len(training_dataset), 'patterns')
    
test_stream = scenario.test_stream

for experience in test_stream:
    task = experience.task_label
    exp_id = experience.current_experience
    test_dataset = experience.dataset
    print('Task {} batch {} -> test'.format(task, exp_id))
    print('This batch contains', len(test_dataset), 'patterns')

## MI-BMINet

In [17]:
class edgeEEGNetBaseline(t.nn.Module):

    def __init__(self, F1=8, D=2, F2=None, C=8, T=2000, N=4, Nf=64, Nf2=16, p_dropout=0.5, activation='relu', # C=8
                 dropout_type='TimeDropout2D'):
        """
        F1:           Number of spectral filters
        D:            Number of spacial filters (per spectral filter), F2 = F1 * D
        F2:           Number or None. If None, then F2 = F1 * D
        C:            Number of EEG channels
        T:            Number of time samples
        N:            Number of classes
	    Nf:           Size of temporal filter
        p_dropout:    Dropout Probability
        activation:   string, either 'elu' or 'relu'
        dropout_type: string, either 'dropout', 'SpatialDropout2d' or 'TimeDropout2D'
        """
        super(edgeEEGNetBaseline, self).__init__()

        # prepare network constants
        if F2 is None:
            F2 = F1 * D

        # check the activation input
        activation = activation.lower()
        assert activation in ['elu', 'relu']
        print("activation relu?: ", activation)

        # Prepare Dropout Type
        if dropout_type.lower() == 'dropout':
            dropout = t.nn.Dropout
        elif dropout_type.lower() == 'spatialdropout2d':
            dropout = t.nn.Dropout2d
        elif dropout_type.lower() == 'timedropout2d':
            dropout = TimeDropout2d
        else:
            raise ValueError("dropout_type must be one of SpatialDropout2d, Dropout or "
                             "WrongDropout2d")

        # store local values
        self.F1, self.D, self.F2, self.C, self.T, self.N = (F1, D, F2, C, T, N)
        self.p_dropout, self.activation = (p_dropout, activation)

        # Number of input neurons to the final fully connected layer
        n_features = (T // 8) // 8 #23 #(T // 8) // 8 

        # Block 1
        self.conv1 = t.nn.Conv2d(1, F1, (C, 1), bias=False)
        self.batch_norm1 = t.nn.BatchNorm2d(F1, momentum=0.01, eps=0.001)
        self.conv2_pad = t.nn.ZeroPad2d((Nf//2-1, Nf//2, 0, 0)) 
        self.conv2 = t.nn.Conv2d(F1, D * F1, (1, Nf), groups=F1, bias=False)
        self.batch_norm2 = t.nn.BatchNorm2d(D * F1, momentum=0.01, eps=0.001)
        self.activation1 = t.nn.ELU(inplace=True) if activation == 'elu' else t.nn.ReLU(inplace=True)
        self.pool1 = t.nn.AvgPool2d((1, 8))
        self.dropout1 = t.nn.Dropout(p=p_dropout)

        # Block 2
        self.sep_conv_pad = t.nn.ZeroPad2d((7, 8, 0, 0))
        self.sep_conv1 = t.nn.Conv2d(D * F1, D * F1, (1, 16), groups=D * F1, bias=False)
        self.sep_conv2 = t.nn.Conv2d(D * F1, F2, (1, 1), bias=False)
        self.batch_norm3 = t.nn.BatchNorm2d(F2, momentum=0.01, eps=0.001)
        self.activation2 = t.nn.ELU(inplace=True) if activation == 'elu' else t.nn.ReLU(inplace=True)
        self.pool2 = t.nn.AvgPool2d((1, 8))
        self.dropout2 = dropout(p=p_dropout)

        # Fully connected layer (classifier)
        self.flatten = t.nn.Flatten()
        self.fc = t.nn.Linear(F2 * n_features, N, bias=True)

        # initialize weights
        self._initialize_params()

    def forward(self, x, with_stats=False):

        # input dimensions: (s, 1, C, T) [batchsize, 1, numb of Channels, T]

        # Block 1
        
        x = self.conv1(x)            # output dim: (s, F1, C, T-1) [batchsize, F1, 1, T]
        x = self.batch_norm1(x)      #[batchsize, F1, 1, T]
        x = self.conv2_pad(x)        
        x = self.conv2(x)            
        
        x = self.batch_norm2(x)
        x = self.activation1(x)
        x = self.pool1(x)            # output dim: (s, D * F1, 1, T // 8)
        x = self.dropout1(x)

        # Block2
        x = self.sep_conv_pad(x)
        x = self.sep_conv1(x)        # output dim: (s, D * F1, 1, T // 8 - 1)
        x = self.sep_conv2(x)        # output dim: (s, F2, 1, T // 8 - 1)
        
        x = self.batch_norm3(x)
        x = self.activation2(x)
        x = self.pool2(x)            # output dim: (s, F2, 1, T // 64)
        x = self.dropout2(x)
        

        # Classification
        x = self.flatten(x)          # output dim: (s, F2 * (T // 64))
        x = self.fc(x)               # output dim: (s, N)
        
        ## Only if we need to store weights of the network
        #if with_stats:
        #    stats = [('conv1_w', self.conv1.weight.data),
        #             ('conv2_w', self.conv2.weight.data),
        #             ('sep_conv1_w', self.sep_conv1.weight.data),
        #             ('sep_conv2_w', self.sep_conv2.weight.data),
        #             ('fc_w', self.fc.weight.data),
        #             ('fc_b', self.fc.bias.data)]
        #    return stats, x
        return x

    def forward_with_tensor_stats(self, x):
        return self.forward(x, with_stats=True)

    def _initialize_params(self, weight_init=t.nn.init.xavier_uniform_, bias_init=t.nn.init.zeros_):
        """
        Initializes all the parameters of the model

        Parameters:
         - weight_init: t.nn.init inplace function
         - bias_init:   t.nn.init inplace function

        """
        def init_weight(m):
            if isinstance(m, t.nn.Conv2d) or isinstance(m, t.nn.Linear):
                weight_init(m.weight)
            if isinstance(m, t.nn.Linear):
                bias_init(m.bias)

        self.apply(init_weight)

class Flatten(t.nn.Module):
    def forward(self, input):
        return input.view(input.size(0), -1)

class TimeDropout2d(t.nn.Dropout2d):
    """
    Dropout layer, where the last dimension is treated as channels
    """
    def __init__(self, p=0.5, inplace=False):
        """
        See t.nn.Dropout2d for parameters
        """
        super(TimeDropout2d, self).__init__(p=p, inplace=inplace)

    def forward(self, input):
        if self.training:
            input = input.permute(0, 3, 1, 2)
            input = F.dropout2d(input, self.p, True, self.inplace)
            input = input.permute(0, 2, 3, 1)
        return input

In [18]:
from avalanche.training.supervised import Naive, CWRStar, Replay, GDumb, Cumulative, LwF, GEM, AGEM, EWC  # and many more!

In [19]:
manualSeed = 4
torch.manual_seed(manualSeed)
random.seed(manualSeed)
np.random.seed(manualSeed)

In [20]:
# Not used yet, change network initialization seeds
from avalanche.training.utils import get_last_fc_layer, freeze_up_to
from avalanche.core import SupervisedPlugin

## Naive TL

In [ ]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    confusion_matrix_metrics,
    class_accuracy_metrics,
    timing_metrics,
    ram_usage_metrics,
    MAC_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    confusion_matrix_metrics(save_image=False, normalize="all", stream=True),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1,2,3]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)



full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = Naive(
        model, optimizer, loss_fn, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
        all_metrics = cl_strategy.evaluator.get_all_metrics()
        print(f"Stored metrics: {list(all_metrics.keys())}")

        
    full_results.append(results)

In [29]:
full_results

[[{'Top1_Acc_MB/train_phase/train_stream/Task000': 1.0,
   'Top1_RunningAcc_Epoch/train_phase/train_stream/Task000': 0.89,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0': 0.86,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1': 0.86,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2': 0.96,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3': 0.88,
   'Top1_Acc_Epoch/train_phase/train_stream/Task000': 0.89,
   'Time_Epoch/train_phase/train_stream/Task000': 5.724486500000239,
   'MaxRAMUsage_Epoch/train_phase/train_stream/Task000': 444.859375,
   'Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/2': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/3': 1.0,
   'Time_Exp/eval_phase/test_stream/Task000/E

In [30]:
#Accuracy
exp_val = np.zeros((4,4,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    
for i in range(4):
    for j in range(4):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))

Avg. ± Std. for exp 0 val 0: 99.75±0.50% 
Avg. ± Std. for exp 0 val 1: 33.25±3.84% 
Avg. ± Std. for exp 0 val 2: 47.75±6.04% 
Avg. ± Std. for exp 0 val 3: 40.25±3.48% 
Avg. ± Std. for exp 1 val 0: 69.00±1.22% 
Avg. ± Std. for exp 1 val 1: 62.25±4.83% 
Avg. ± Std. for exp 1 val 2: 54.50±5.10% 
Avg. ± Std. for exp 1 val 3: 52.00±6.92% 
Avg. ± Std. for exp 2 val 0: 66.75±3.67% 
Avg. ± Std. for exp 2 val 1: 65.00±2.96% 
Avg. ± Std. for exp 2 val 2: 67.75±3.98% 
Avg. ± Std. for exp 2 val 3: 58.00±7.85% 
Avg. ± Std. for exp 3 val 0: 61.50±7.13% 
Avg. ± Std. for exp 3 val 1: 68.25±2.57% 
Avg. ± Std. for exp 3 val 2: 66.75±1.70% 
Avg. ± Std. for exp 3 val 3: 61.75±5.79% 


## Replay (buf=20)

In [32]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    confusion_matrix_metrics,
    class_accuracy_metrics,
    timing_metrics,
    ram_usage_metrics,
    MAC_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    confusion_matrix_metrics(save_image=False, normalize="all", stream=True),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1,2,3]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)


full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = Replay(
        model, optimizer, loss_fn, mem_size=20, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1, 2, 3]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.40it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 185.4531
	Time_Epoch/train_phase/train_stream/Task000 = 3.1219
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.2550
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.1000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.2550
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.1400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.2200
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.4000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.2600
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.04it/s]
Epoch 1 end

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.07it/s]
Epoch 12 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 185.6250
	Time_Epoch/train_phase/train_stream/Task000 = 3.2922
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7700
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.7700
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7800
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.6600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.7600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.8800
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.06it/s]
Epoch 13 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 185.6250
	Time_Epoch/train_phase/train_stream/Task000 = 3.3015
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.22it/s]
Epoch 24 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 185.6016
	Time_Epoch/train_phase/train_stream/Task000 = 3.2135
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8550
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8550
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.8800
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9600
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.19it/s]
Epoch 25 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 185.6055
	Time_Epoch/train_phase/train_stream/Task000 = 3.2303
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  5.90it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 185.4492
	Time_Epoch/train_phase/train_stream/Task000 = 3.3889
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9250
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9250
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 1.0000
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.24it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 184.7695
	Time_Epoch/train_phase/train_stream/Task000 = 3.2029
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.26it/s]
Epoch 3 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 204.6211
	Time_Epoch/train_phase/train_stream/Task000 = 3.6835
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8125
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8125
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7167
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7037
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9103
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.8958
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.30it/s]
Epoch 4 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.9961
	Time_Epoch/train_phase/train_stream/Task000 = 3.6344
	Top1_Acc_Epoch/train_phase/tr

...

-- >> End of eval phase << --
	ConfusionMatrix_Stream/eval_phase/test_stream = 
tensor([[0.1000, 0.1125, 0.0281, 0.0094],
        [0.0844, 0.1375, 0.0219, 0.0063],
        [0.0125, 0.0031, 0.2031, 0.0312],
        [0.0125, 0.0156, 0.0219, 0.2000]], dtype=torch.float64)
	MaxRAMUsage_Stream/eval_phase/test_stream/Task000 = 187.2148
	Time_Stream/eval_phase/test_stream/Task000 = 0.6745
	Top1_Acc_Stream/eval_phase/test_stream/Task000 = 0.6406
Start of experience:  3
Current Classes:  [0, 1, 2, 3]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.32it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 207.5430
	Time_Epoch/train_phase/train_stream/Task000 = 3.6100
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.6500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningClassAcc_Epoch/train_pha

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.29it/s]
Epoch 11 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 207.5430
	Time_Epoch/train_phase/train_stream/Task000 = 3.6439
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9042
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9042
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8788
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9762
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9259
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.33it/s]
Epoch 12 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 207.5547
	Time_Epoch/train_phase/train_stream/Task000 = 3.6008
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.26it/s]
Epoch 23 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 207.5742
	Time_Epoch/train_phase/train_stream/Task000 = 3.6839
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9625
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9625
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9167
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9848
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9762
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9444
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.21it/s]
Epoch 24 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 211.3516
	Time_Epoch/train_phase/train_stream/Task000 = 3.7392
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.27it/s]
Epoch 35 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 207.6680
	Time_Epoch/train_phase/train_stream/Task000 = 3.6631
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9417
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9417
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8056
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9545
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9643
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9815
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.32it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 207.6680
	Time_Epoch/train_phase/train_stream/Task000 = 3.6165
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.23it/s]
Epoch 47 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 207.6680
	Time_Epoch/train_phase/train_stream/Task000 = 3.7189
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9750
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9750
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9167
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9697
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9881
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 1.0000
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.26it/s]
Epoch 48 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 211.4453
	Time_Epoch/train_phase/train_stream/Task000 = 3.6770
	Top1_Acc_Epoch/train_phase/

In [33]:
full_results

[[{'Top1_Acc_MB/train_phase/train_stream/Task000': 1.0,
   'Top1_RunningAcc_Epoch/train_phase/train_stream/Task000': 0.89,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0': 0.86,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1': 0.86,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2': 0.96,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3': 0.88,
   'Top1_Acc_Epoch/train_phase/train_stream/Task000': 0.89,
   'Time_Epoch/train_phase/train_stream/Task000': 3.310919399999875,
   'MaxRAMUsage_Epoch/train_phase/train_stream/Task000': 184.8046875,
   'Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/2': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/3': 1.0,
   'Time_Exp/eval_phase/test_stream/Task000/

In [34]:
#Accuracy
exp_val = np.zeros((4,4,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    
for i in range(4):
    for j in range(4):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))

Avg. ± Std. for exp 0 val 0: 99.75±0.50% 
Avg. ± Std. for exp 0 val 1: 33.25±3.84% 
Avg. ± Std. for exp 0 val 2: 47.75±6.04% 
Avg. ± Std. for exp 0 val 3: 40.25±3.48% 
Avg. ± Std. for exp 1 val 0: 84.75±4.83% 
Avg. ± Std. for exp 1 val 1: 63.00±3.41% 
Avg. ± Std. for exp 1 val 2: 60.50±2.45% 
Avg. ± Std. for exp 1 val 3: 52.50±3.95% 
Avg. ± Std. for exp 2 val 0: 71.50±4.77% 
Avg. ± Std. for exp 2 val 1: 66.00±3.82% 
Avg. ± Std. for exp 2 val 2: 64.25±4.00% 
Avg. ± Std. for exp 2 val 3: 59.75±4.06% 
Avg. ± Std. for exp 3 val 0: 66.00±8.49% 
Avg. ± Std. for exp 3 val 1: 67.75±4.29% 
Avg. ± Std. for exp 3 val 2: 66.00±3.66% 
Avg. ± Std. for exp 3 val 3: 56.25±6.89% 


## Replay (buf=200)

In [36]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    confusion_matrix_metrics,
    class_accuracy_metrics,
    MAC_metrics,
    timing_metrics,
    ram_usage_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    confusion_matrix_metrics(save_image=False, normalize="all", stream=True),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1,2,3]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)

full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = Replay(
        model, optimizer, loss_fn, mem_size=200, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1, 2, 3]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.39it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.5195
	Time_Epoch/train_phase/train_stream/Task000 = 3.1293
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.2550
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.1000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.2550
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.1400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.2200
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.4000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.2600
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.12it/s]
Epoch 1 end

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.23it/s]
Epoch 12 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.5273
	Time_Epoch/train_phase/train_stream/Task000 = 3.2052
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7700
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.7700
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7800
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.6600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.7600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.8800
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.07it/s]
Epoch 13 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.5352
	Time_Epoch/train_phase/train_stream/Task000 = 3.2926
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.10it/s]
Epoch 24 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.5781
	Time_Epoch/train_phase/train_stream/Task000 = 3.2759
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8550
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8550
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.8800
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9600
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.24it/s]
Epoch 25 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.5781
	Time_Epoch/train_phase/train_stream/Task000 = 3.2067
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.14it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.5898
	Time_Epoch/train_phase/train_stream/Task000 = 3.2547
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9250
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9250
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 1.0000
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.15it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 197.5898
	Time_Epoch/train_phase/train_stream/Task000 = 3.2521
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.28it/s]
Epoch 3 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 208.4062
	Time_Epoch/train_phase/train_stream/Task000 = 3.6596
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7708
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.7708
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.6500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.6000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9492
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.8852
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.29it/s]
Epoch 4 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 208.4062
	Time_Epoch/train_phase/train_stream/Task000 = 3.6504
	Top1_Acc_Epoch/train_phase/tr

...

-- >> End of eval phase << --
	ConfusionMatrix_Stream/eval_phase/test_stream = 
tensor([[0.1281, 0.1094, 0.0125, 0.0000],
        [0.0906, 0.1562, 0.0000, 0.0031],
        [0.0219, 0.0125, 0.2031, 0.0125],
        [0.0312, 0.0281, 0.0125, 0.1781]], dtype=torch.float64)
	MaxRAMUsage_Stream/eval_phase/test_stream/Task000 = 189.4141
	Time_Stream/eval_phase/test_stream/Task000 = 0.7247
	Top1_Acc_Stream/eval_phase/test_stream/Task000 = 0.6656
Start of experience:  3
Current Classes:  [0, 1, 2, 3]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.38it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 209.7422
	Time_Epoch/train_phase/train_stream/Task000 = 3.5462
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7417
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.7417
	Top1_RunningClassAcc_Epoch/train_pha

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.25it/s]
Epoch 11 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 209.7422
	Time_Epoch/train_phase/train_stream/Task000 = 3.6944
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8750
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8750
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7895
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.8871
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9508
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.26it/s]
Epoch 12 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 209.7422
	Time_Epoch/train_phase/train_stream/Task000 = 3.6777
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.29it/s]
Epoch 23 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 209.7422
	Time_Epoch/train_phase/train_stream/Task000 = 3.6508
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8917
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8917
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8852
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8077
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9219
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9365
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.30it/s]
Epoch 24 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 209.7422
	Time_Epoch/train_phase/train_stream/Task000 = 3.6292
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.26it/s]
Epoch 35 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 209.7422
	Time_Epoch/train_phase/train_stream/Task000 = 3.6835
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8909
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8036
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9231
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9688
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.33it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 209.7422
	Time_Epoch/train_phase/train_stream/Task000 = 3.6037
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.28it/s]
Epoch 47 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 209.7422
	Time_Epoch/train_phase/train_stream/Task000 = 3.6523
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8958
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.7500
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8958
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8971
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9825
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.8727
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:03<00:00,  3.23it/s]
Epoch 48 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 209.7422
	Time_Epoch/train_phase/train_stream/Task000 = 3.7160
	Top1_Acc_Epoch/train_phase/

In [37]:
full_results

[[{'Top1_Acc_MB/train_phase/train_stream/Task000': 1.0,
   'Top1_RunningAcc_Epoch/train_phase/train_stream/Task000': 0.89,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0': 0.86,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1': 0.86,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2': 0.96,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3': 0.88,
   'Top1_Acc_Epoch/train_phase/train_stream/Task000': 0.89,
   'Time_Epoch/train_phase/train_stream/Task000': 3.3255547000007937,
   'MaxRAMUsage_Epoch/train_phase/train_stream/Task000': 197.59375,
   'Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/2': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/3': 1.0,
   'Time_Exp/eval_phase/test_stream/Task000/E

In [38]:
#Accuracy
exp_val = np.zeros((4,4,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    
for i in range(4):
    for j in range(4):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))

Avg. ± Std. for exp 0 val 0: 99.75±0.50% 
Avg. ± Std. for exp 0 val 1: 33.25±3.84% 
Avg. ± Std. for exp 0 val 2: 47.75±6.04% 
Avg. ± Std. for exp 0 val 3: 40.25±3.48% 
Avg. ± Std. for exp 1 val 0: 99.25±1.00% 
Avg. ± Std. for exp 1 val 1: 54.25±2.57% 
Avg. ± Std. for exp 1 val 2: 63.25±2.18% 
Avg. ± Std. for exp 1 val 3: 51.00±5.61% 
Avg. ± Std. for exp 2 val 0: 92.75±3.39% 
Avg. ± Std. for exp 2 val 1: 64.75±3.98% 
Avg. ± Std. for exp 2 val 2: 64.75±3.98% 
Avg. ± Std. for exp 2 val 3: 54.50±7.97% 
Avg. ± Std. for exp 3 val 0: 86.25±3.06% 
Avg. ± Std. for exp 3 val 1: 67.75±6.19% 
Avg. ± Std. for exp 3 val 2: 64.00±4.43% 
Avg. ± Std. for exp 3 val 3: 59.00±6.04% 


## LwF

In [40]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    confusion_matrix_metrics,
    class_accuracy_metrics,
    MAC_metrics,
    timing_metrics,
    ram_usage_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    confusion_matrix_metrics(save_image=False, normalize="all", stream=True),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1,2,3]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)


full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = LwF(
        model, optimizer, loss_fn, alpha=1, temperature=2, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1, 2, 3]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.23it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 199.2656
	Time_Epoch/train_phase/train_stream/Task000 = 3.2093
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.2550
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.1000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.2550
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.1400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.2200
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.4000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.2600
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  5.98it/s]
Epoch 1 end

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.07it/s]
Epoch 12 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 199.2695
	Time_Epoch/train_phase/train_stream/Task000 = 3.2928
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7700
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.7700
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7800
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.6600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.7600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.8800
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.17it/s]
Epoch 13 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 199.2695
	Time_Epoch/train_phase/train_stream/Task000 = 3.2423
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.03it/s]
Epoch 24 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 199.2734
	Time_Epoch/train_phase/train_stream/Task000 = 3.3146
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8550
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8550
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.8800
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9600
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.04it/s]
Epoch 25 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 199.2734
	Time_Epoch/train_phase/train_stream/Task000 = 3.3116
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.06it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 199.2734
	Time_Epoch/train_phase/train_stream/Task000 = 3.2966
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9250
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9250
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 1.0000
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  5.94it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 199.2734
	Time_Epoch/train_phase/train_stream/Task000 = 3.3640
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.44it/s]
Epoch 3 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.3203
	Time_Epoch/train_phase/train_stream/Task000 = 2.2019
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7583
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.7583
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.5667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.8667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.8000
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.45it/s]
Epoch 4 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.8438
	Time_Epoch/train_phase/train_stream/Task000 = 2.2020
	Top1_Acc_Epoch/train_phase/tr

...

-- >> End of eval phase << --
	ConfusionMatrix_Stream/eval_phase/test_stream = 
tensor([[0.0875, 0.1094, 0.0437, 0.0094],
        [0.0688, 0.1406, 0.0344, 0.0063],
        [0.0063, 0.0063, 0.2188, 0.0187],
        [0.0125, 0.0219, 0.0281, 0.1875]], dtype=torch.float64)
	MaxRAMUsage_Stream/eval_phase/test_stream/Task000 = 190.8047
	Time_Stream/eval_phase/test_stream/Task000 = 0.5990
	Top1_Acc_Stream/eval_phase/test_stream/Task000 = 0.6344
Start of experience:  3
Current Classes:  [0, 1, 2, 3]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.90it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 202.5078
	Time_Epoch/train_phase/train_stream/Task000 = 2.0314
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.5250
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.6000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.5250
	Top1_RunningClassAcc_Epoch/train_pha

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.27it/s]
Epoch 11 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.3867
	Time_Epoch/train_phase/train_stream/Task000 = 2.2756
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8250
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8250
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.7333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9000
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.56it/s]
Epoch 12 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.3867
	Time_Epoch/train_phase/train_stream/Task000 = 2.1567
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.46it/s]
Epoch 23 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.3867
	Time_Epoch/train_phase/train_stream/Task000 = 2.1951
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.6000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9333
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.67it/s]
Epoch 24 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.3867
	Time_Epoch/train_phase/train_stream/Task000 = 2.1169
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.46it/s]
Epoch 35 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.3867
	Time_Epoch/train_phase/train_stream/Task000 = 2.1965
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 1.0000
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.55it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.2266
	Time_Epoch/train_phase/train_stream/Task000 = 2.1577
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.62it/s]
Epoch 47 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.3867
	Time_Epoch/train_phase/train_stream/Task000 = 2.1326
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9500
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.9667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 1.0000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9333
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.57it/s]
Epoch 48 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 205.0273
	Time_Epoch/train_phase/train_stream/Task000 = 2.1530
	Top1_Acc_Epoch/train_phase/

In [41]:
full_results

[[{'Top1_Acc_MB/train_phase/train_stream/Task000': 1.0,
   'Top1_RunningAcc_Epoch/train_phase/train_stream/Task000': 0.89,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0': 0.86,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1': 0.86,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2': 0.96,
   'Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3': 0.88,
   'Top1_Acc_Epoch/train_phase/train_stream/Task000': 0.89,
   'Time_Epoch/train_phase/train_stream/Task000': 3.2822087000004103,
   'MaxRAMUsage_Epoch/train_phase/train_stream/Task000': 199.27734375,
   'Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/0': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/1': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/2': 1.0,
   'Top1_ClassAcc_Exp/eval_phase/test_stream/Task000/Exp000/3': 1.0,
   'Time_Exp/eval_phase/test_stream/Task00

In [42]:
#Accuracy
exp_val = np.zeros((4,4,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    
for i in range(4):
    for j in range(4):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))

Avg. ± Std. for exp 0 val 0: 99.75±0.50% 
Avg. ± Std. for exp 0 val 1: 33.25±3.84% 
Avg. ± Std. for exp 0 val 2: 47.75±6.04% 
Avg. ± Std. for exp 0 val 3: 40.25±3.48% 
Avg. ± Std. for exp 1 val 0: 78.25±4.00% 
Avg. ± Std. for exp 1 val 1: 57.50±3.54% 
Avg. ± Std. for exp 1 val 2: 55.25±2.00% 
Avg. ± Std. for exp 1 val 3: 49.50±4.78% 
Avg. ± Std. for exp 2 val 0: 72.75±5.21% 
Avg. ± Std. for exp 2 val 1: 60.75±4.78% 
Avg. ± Std. for exp 2 val 2: 66.75±2.81% 
Avg. ± Std. for exp 2 val 3: 57.50±5.97% 
Avg. ± Std. for exp 3 val 0: 68.50±0.94% 
Avg. ± Std. for exp 3 val 1: 60.75±5.34% 
Avg. ± Std. for exp 3 val 2: 67.00±3.50% 
Avg. ± Std. for exp 3 val 3: 61.25±2.09% 


## EWC

In [44]:
from avalanche.evaluation.metrics import (
    accuracy_metrics,
    confusion_matrix_metrics,
    timing_metrics,
    ram_usage_metrics,
    class_accuracy_metrics,
    MAC_metrics,
)

from avalanche.training.plugins import EvaluationPlugin

from avalanche.logging import InteractiveLogger, TextLogger, CSVLogger

class ModifyEpochsP(SupervisedPlugin):

    def __init__(self):
        super().__init__()

    def after_training_exp(self, strategy, **kwargs):
        """
        Train epochs fixed as 100.
        """
        strategy.train_epochs = 50

        
# log to text file
text_logger = TextLogger(open("log.txt", "a"))

# print to stdout
interactive_logger = InteractiveLogger()

csv_logger = CSVLogger()
        
eval_plugin = EvaluationPlugin(
    accuracy_metrics(
        minibatch=True,
        epoch=True,
        epoch_running=True,
        experience=True,
        stream=True,
    ),
    confusion_matrix_metrics(save_image=False, normalize="all", stream=True),
    class_accuracy_metrics(epoch_running=True, experience=True, classes=[0,1,2,3]),
    timing_metrics(
        epoch=True,
        experience=True,
        stream=True
    ),
    ram_usage_metrics(
        epoch=True, experience=True, stream=True
    ),
    loggers=[interactive_logger, text_logger, csv_logger],
    collect_all=True,
)

full_results = []

for manualSeed in range(5):
    
    print('Rand Seed: {}'.format(manualSeed))
    
    os.environ['PYTHONHASHSEED'] = str(manualSeed)
    torch.manual_seed(manualSeed)
    random.seed(manualSeed)
    np.random.seed(manualSeed)
    torch.backends.cudnn.deterministic = True
    
    model = edgeEEGNetBaseline(**config['indiv']['net']['params'])

    loss_fn = torch.nn.modules.loss.CrossEntropyLoss(**config['indiv']['loss_function']['params'])

    optimizer = optim.Adam(model.parameters(), lr=1e-3, eps=1e-7)

    cl_strategy = EWC(
        model, optimizer, loss_fn, ewc_lambda=10000, train_mb_size=10, eval_mb_size=10,
        train_epochs=40, plugins=[ModifyEpochsP()], evaluator=eval_plugin
    )

    # TRAINING LOOP
    print('Starting experiment...')
    results = []
    for experience in scenario.train_stream:
        print("Start of experience: ", experience.current_experience)
        print("Current Classes: ", experience.classes_in_this_experience)

        cl_strategy.train(experience)
        print('Training completed')

        print('Computing accuracy on the whole test set')
        results.append(cl_strategy.eval(scenario.test_stream))
        
    full_results.append(results)

Rand Seed: 0
activation relu?:  relu
Starting experiment...
Start of experience:  0
Current Classes:  [0, 1, 2, 3]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.46it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.7852
	Time_Epoch/train_phase/train_stream/Task000 = 3.0951
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.2550
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.1000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.2550
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.1400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.2200
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.4000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.2600
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.07it/s]
Epoch 1 end

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.16it/s]
Epoch 12 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.7891
	Time_Epoch/train_phase/train_stream/Task000 = 3.2436
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.7700
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.8000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.7700
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7800
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.6600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.7600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.8800
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.09it/s]
Epoch 13 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.7891
	Time_Epoch/train_phase/train_stream/Task000 = 3.2820
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.16it/s]
Epoch 24 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.7891
	Time_Epoch/train_phase/train_stream/Task000 = 3.2456
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.8550
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.9000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.8550
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.7400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.8400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.8800
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.9600
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.28it/s]
Epoch 25 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.7891
	Time_Epoch/train_phase/train_stream/Task000 = 3.1814
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.07it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 203.2500
	Time_Epoch/train_phase/train_stream/Task000 = 3.2964
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.9250
	Top1_Acc_MB/train_phase/train_stream/Task000 = 1.0000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.9250
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.8600
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.9000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.9400
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 1.0000
100%|██████████████████████████████████████████████████████████████████████████████████| 20/20 [00:03<00:00,  6.18it/s]
Epoch 37 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 200.7969
	Time_Epoch/train_phase/train_stream/Task000 = 3.2344
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:01<00:00,  6.06it/s]
Epoch 3 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.0898
	Time_Epoch/train_phase/train_stream/Task000 = 1.9786
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.6000
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.7000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.6000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.5000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.5667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.6000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.7333
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:01<00:00,  6.06it/s]
Epoch 4 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.0898
	Time_Epoch/train_phase/train_stream/Task000 = 1.9782
	Top1_Acc_Epoch/train_phase/tr

...

-- >> End of eval phase << --
	ConfusionMatrix_Stream/eval_phase/test_stream = 
tensor([[0.1344, 0.0531, 0.0281, 0.0344],
        [0.0938, 0.1156, 0.0281, 0.0125],
        [0.0219, 0.0125, 0.1969, 0.0187],
        [0.0469, 0.0187, 0.0500, 0.1344]], dtype=torch.float64)
	MaxRAMUsage_Stream/eval_phase/test_stream/Task000 = 191.8438
	Time_Stream/eval_phase/test_stream/Task000 = 0.6352
	Top1_Acc_Stream/eval_phase/test_stream/Task000 = 0.5813
Start of experience:  3
Current Classes:  [0, 1, 2, 3]
-- >> Start of training phase << --
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:01<00:00,  6.44it/s]
Epoch 0 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.4180
	Time_Epoch/train_phase/train_stream/Task000 = 1.8609
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.4083
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.5000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.4083
	Top1_RunningClassAcc_Epoch/train_pha

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.84it/s]
Epoch 11 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.4180
	Time_Epoch/train_phase/train_stream/Task000 = 2.0513
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.4250
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.2000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.4250
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.3667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.3667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.5333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.4333
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.68it/s]
Epoch 12 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.4180
	Time_Epoch/train_phase/train_stream/Task000 = 2.1086
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.96it/s]
Epoch 23 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.4180
	Time_Epoch/train_phase/train_stream/Task000 = 2.0118
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.4167
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.4000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.4167
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.4333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.2333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.6000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.4000
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.76it/s]
Epoch 24 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.2617
	Time_Epoch/train_phase/train_stream/Task000 = 2.0827
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.90it/s]
Epoch 35 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.4180
	Time_Epoch/train_phase/train_stream/Task000 = 2.0326
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.3833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.2000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.3833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.3000
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.3667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.5333
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.3333
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.93it/s]
Epoch 36 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.4180
	Time_Epoch/train_phase/train_stream/Task000 = 2.0207
	Top1_Acc_Epoch/train_phase/

100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.87it/s]
Epoch 47 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.4180
	Time_Epoch/train_phase/train_stream/Task000 = 2.0439
	Top1_Acc_Epoch/train_phase/train_stream/Task000 = 0.3833
	Top1_Acc_MB/train_phase/train_stream/Task000 = 0.5000
	Top1_RunningAcc_Epoch/train_phase/train_stream/Task000 = 0.3833
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/0 = 0.3667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/1 = 0.2667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/2 = 0.5667
	Top1_RunningClassAcc_Epoch/train_phase/train_stream/Task000/3 = 0.3333
100%|██████████████████████████████████████████████████████████████████████████████████| 12/12 [00:02<00:00,  5.86it/s]
Epoch 48 ended.
	MaxRAMUsage_Epoch/train_phase/train_stream/Task000 = 201.4180
	Time_Epoch/train_phase/train_stream/Task000 = 2.0438
	Top1_Acc_Epoch/train_phase/

In [45]:
#Accuracy
exp_val = np.zeros((4,4,5))

for item_no in range(len(full_results)):

    exp_val[0,0,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[0,1,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[0,2,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[0,3,item_no] = (full_results[item_no][0]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[1,0,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[1,1,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[1,2,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[1,3,item_no] = (full_results[item_no][1]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[2,0,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[2,1,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[2,2,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[2,3,item_no] = (full_results[item_no][2]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    exp_val[3,0,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp000'])
    exp_val[3,1,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp001'])
    exp_val[3,2,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp002'])
    exp_val[3,3,item_no] = (full_results[item_no][3]['Top1_Acc_Exp/eval_phase/test_stream/Task000/Exp003'])
    
for i in range(4):
    for j in range(4):
        print("Avg. ± Std. for exp {} val {}: {:.2f}±{:.2f}% ".format(i, j, np.array(exp_val[i,j]).mean()*100, np.array(exp_val[i,j]).std()*100))
        #print("Std. for exp {} val {}: {}".format(i, j, np.array(exp_val[i,j]).std()))

Avg. ± Std. for exp 0 val 0: 99.75±0.50% 
Avg. ± Std. for exp 0 val 1: 33.25±3.84% 
Avg. ± Std. for exp 0 val 2: 47.75±6.04% 
Avg. ± Std. for exp 0 val 3: 40.25±3.48% 
Avg. ± Std. for exp 1 val 0: 94.75±2.42% 
Avg. ± Std. for exp 1 val 1: 49.25±4.65% 
Avg. ± Std. for exp 1 val 2: 48.00±3.92% 
Avg. ± Std. for exp 1 val 3: 42.25±5.21% 
Avg. ± Std. for exp 2 val 0: 94.00±1.84% 
Avg. ± Std. for exp 2 val 1: 43.50±4.43% 
Avg. ± Std. for exp 2 val 2: 53.50±3.10% 
Avg. ± Std. for exp 2 val 3: 46.00±5.09% 
Avg. ± Std. for exp 3 val 0: 94.75±3.91% 
Avg. ± Std. for exp 3 val 1: 34.25±2.57% 
Avg. ± Std. for exp 3 val 2: 52.25±3.30% 
Avg. ± Std. for exp 3 val 3: 40.25±3.57% 
